In [76]:
from tools import *

# Chiffrement TLWE

In [126]:
def TLWEncrypt(p,q,n,s,sigma,m):
    a=[]
    for i in range(n):
        a.append(randint(0,q-1))
    e = RealDistribution("gaussian",sigma).get_random_element()
    e = round(q*e)
    while(abs(e/q)>=1/(2*p)):
        e = RealDistribution("gaussian",sigma).get_random_element()
        e = round(q*e)
    #print("e= ",e)
    #e=0
    c = AddInTore(q,m*q/p,e)
    for i in range(n):
        c = AddInTore(q,c,MultExtTore(q,s[i],a[i]))
    return a+[c]

In [127]:
def TLWEDecrypt(p,q,n,s,c):
    a = c[:-1]
    m = c[-1]
    for i in range(n):
        m = AddInTore(q,m,MultExtTore(q,-s[i],a[i]))
    return round(m*p/q)%p

In [79]:
p = 2
q = 2**32
n = 1000
s = [randint(0,1) for i in range(n)]
sigma = 2**(-7)

cpt = 0
for i in range(1000):
    
    m = randint(0,p-1)


    c = TLWEncrypt(p, q, n, s, sigma, m)

    mmaybe = TLWEDecrypt(p, q, n, s, c)
    if(m==mmaybe):
        cpt = cpt +1
print(cpt)        

1000


## Addition de chiffrés et mutliplication par une constante

In [80]:
def AddCiph(q,n,c1,c2):
    return [AddInTore(q,c1[i],c2[i]) for i in range(n+1)]

In [81]:
def MultCiph(q,n,K,c):
    return [MultExtTore(q,K,c[i]) for i in range(n+1)]

Test : $TLWE_s(m_1) + TLWE_s(m_2) = TLWE_s(m_1+m_2)$

In [82]:
p = 2**9
q = 2**16
n = 1000
s = [randint(0,1) for i in range(n)]
sigma = 2**(-7)

cpt1 = 0
cpt2 = 0
for i in range(100):
    
    m1 = randint(0,p-1)
    m2 = randint(0,p-1)

    c1 = TLWEncrypt(p, q, n, s, sigma, m1)
    c2 = TLWEncrypt(p, q, n, s, sigma, m2)

    m = TLWEDecrypt(p, q, n, s, AddCiph(q,n,c1,c2))
    if(m==AddInTore(p,m1,m2)):
        cpt1 = cpt1 +1
print(cpt1)

100


Test : $TLWE_s(m) \cdot K = TLWE_s(m \cdot K)$

In [83]:
p = 2
q = 2**32
n = 1000
s = [randint(0,1) for i in range(n)]
sigma = 2**(-7)

cpt1 = 0
cpt2 = 0
for i in range(100):
    
    m = randint(0,p-1)

    c = TLWEncrypt(p, q, n, s, sigma, m)
    
    K = randint(1,100)
    mmaybe = TLWEDecrypt(p, q, n, s, MultCiph(q,n,K,c))
    
    if(mmaybe==MultExtTore(p,K,m)):
        cpt1 +=1
print(cpt1)

100


## Multiplication de chiffrés : Gadget Matrix

In [84]:
#G is the gadhet matrix of the numerator of the real gadget matrix with q for denominator
def GadgetMatrix(q,B,l,n):
    G = [[0 for i in range(n+1)] for j in range((n+1)*l)]
    for i in range(n+1):
        for j in range(0,l):
            G[j+l*i][i] = q/(B^(j+1))
    return G

In [85]:
def InvGVect(q,B,l,n,v):
    for i in range(len(v)) :
        if v[i]> q/2 :
            v[i] = v[i]-q
    vbar = [round(B**l*v[i]/q) for i in range(len(v))]
    u=[]
    for i in range(len(v)) :
        tmp = (vbar[i]).digits(B)
        while (len(tmp)!=l+1) :
            tmp.append(0)
        for j in range(len(tmp)-1) :
            if tmp[j]>= ceil(B/2) :
                tmp[j] = tmp[j]-B
                tmp[j+1] = tmp[j+1]+1
        tmp.reverse()
        u = u+(tmp[1:])
    return [u]

In [86]:
def InvGMatr(q,B,l,n,M) :
    return [InvGVect(q,B,l,n,M[i]) for i in range(len(M))]

Test : $g^{-1}(v) \cdot G^T = v$ ?

In [87]:
g = InvGVect(64,4,3,1,[41,26])
print(g)
G = GadgetMatrix(64,4,3,1)
MultInMatr(64,g,G)

[[-1, -1, -3, -2, -1, -2]]


[[41, 26]]

## Multiplication de chiffrés : chiffrement TGSW

In [88]:
def TGSWEncrypt(q,B,l,n,sigma,s,m):
    Z = [TLWEncrypt(B**l,q,n,s,sigma,0) for i in range((n+1)*l)]
    return AddInMatr(q,Z,MultExtMatr(q,m,GadgetMatrix(q,B,l,n)))

In [89]:
#Intern product TGSW
#c1 et c2 are TGSW ciphertexts
def MultInGSW(q,B,l,n,c1,c2) :
    return MultInMatr(q,InvGMatr(q,B,l,n,c1),c2)

In [90]:
#Extern product for TLWE
#c1 is TGSW ciphertext
#c2 is TLWE ciphertext
def MultExtCiphLWE(q,B,l,n,c1,c2) :
    return MultInMatr(q,InvGVect(q,B,l,n,c2),c1)

In [91]:
q = 64
B = 4
l = 3
p = B**l
n = 10
sigma = 2**(-5)
cpt=0
for j in range(100) :
    m = randint(0,p-1)
    k = randint(0,p-1)
    s = [randint(0,1) for i in range(n)]
    cm = TLWEncrypt(p,q,n,s,sigma,m)

    ck = TGSWEncrypt(q,B,l,n,sigma,s,k)
    c = MultExtCiphLWE(q,B,l,n,ck,cm)[0]
    
    mmaybe = TLWEDecrypt(p,q,n,s,c)
    
    if mmaybe == MultExtTore(p,k,m) :    
        cpt+=1
print(cpt)


100


# Chiffrement TGLWE

In [92]:
#G^{-1} on a vector polynomes
#vX a vector of poly in TQ_N[X]
def InvGVectPoly(q,B,l,N,vX) :
    result = []
    for poly in vX :
        for i in range(len(poly)):
            if poly[i] > q/2 :
                poly[i] = poly[i]-q
        polybar = [round(B**l*poly[i]/q) for i in range(len(poly))]
        u = [[0]*(N) for _ in range(l)]
        for i in range(len(poly)) :
            tmp = polybar[i].digits(B)
            while (len(tmp)!= l+1) :
                tmp.append(0)
            for j in range(len(tmp)-1) :
                if tmp[j] >= B//2 :
                    tmp[j] = tmp[j] - B
                    tmp[j+1]=tmp[j+1]+1
            tmp.reverse()
            tmp = tmp[1:]
            for index in range(len(tmp)) :
                u[index][i] = u[index][i]+tmp[index]
        result += u
    return [result]

In [93]:
# Returns gadget matrix G^T but with polynoms
def GadgetMatrixPoly(q,B,l,k,N):
    G = [[[0]*N for i in range(k+1)] for j in range((k+1)*l)]
    for i in range(k+1):
        for j in range(0,l):
            G[j+l*i][i][0] = q/(B^(j+1))
    return G

Test : $g^{-1}(p) \cdot G^T \approx p$

In [94]:
k = 1
N = 2
l = 3
B = 4
q = 256
vX = [[41,26],[231,35]]
Ginv = InvGVectPoly(q,B,l,N,vX)
G = GadgetMatrixPoly(q,B,l,k,N)
MultMatPoly(q,N,Ginv,G)

[[[40, 28], [232, 36]]]

In [95]:
#G^{-1} on a matrix of polynomes
def InvGMatrPoly(q,B,l,N,M) :
    return [InvGVectPoly(q,B,l,N,M[i]) for i in range(len(M))]

In [96]:
# TGLWE Encryption
def TGLWEncrypt(p,q,N,k,s,sigma,m) :
    a = []
    for i in range(k) :
        a.append([randint(0,q-1) for j in range(N)])
    e = [RealDistribution("gaussian",sigma).get_random_element() for i in range(N)]
    e = [round(q*e[i]) for i in range(N)]
    M = [m[i]*q/p for i in range(N)]
    c = AddPolyInTore(q,N,M,e)
    for i in range(k):
        c = AddPolyInTore(q,N,c,MultPolyExt(q,N,s[i],a[i]))
    return a+[c]

In [97]:
# TGLWE Decryption
def TGLWEDecrypt(p,q,N,k,s,c) :
    tmp = [0]*N
    for i in range(k) :
        tmp = AddPolyInTore(q,N,tmp,MultPolyExt(q,N,[-(s[i][j]) for j in range(len(s[i]))],c[i]))
    tmp = AddPolyInTore(q,N,tmp,c[len(c)-1])
    result = []
    for i in range(len(tmp)) :
        result.append(round(tmp[i]*p/q)%p)
    return result

In [98]:
# Extern product of TGLWE
#C1 a TGGSW ciphertext (matrix)
#c2 a TGLWE ciphertext (vector)
def MultExtTGLWE(q,N,B,l,C1,c2) :
    return MultMatPoly(q,N,InvGVectPoly(q,B,l,N,c2),C1)

### Chiffrement TGGSW

In [99]:
#TGGSW Encryption
def TGGSWEncrypt(p,q,B,l,N,k,sigma,s,m):
    Z = [TGLWEncrypt(p,q,N,k,s,sigma,[0]*N) for _ in range((k+1)*l)]
    return AddInMatrPoly(q,N,Z,MultExtMatrPoly(q,N,m,GadgetMatrixPoly(q,B,l,k,N)))

# Bootstrapping

In [100]:
# Cb TGGSW ciphertext
# c0,c1 TGLWE ciphertext
def CMUX(q,N,Cb,c0,c1) : 
    tmp = [AddPolyInTore(q,N,c1[i],[-c0[i][ind] for ind in range(len(c0[i]))]) for i in range(len(c0))]
    tmp2 = MultExtTGLWE(q,N,B,l,Cb,tmp)[0]
    return [AddPolyInTore(q,N,tmp2[i],c0[i]) for i in range(len(c0))]

In [106]:
def loadKeys(p,q,B,l,N,sigma,k,S,s) :
    Sprime = []
    for si in S :
        Sprime += si
    bs = [TGGSWEncrypt(p,q,B,l,N,k,sigma,S, [s[i]] + [0]*(N-1)) for i in range(n)]
    ks = [[_ for j in range(l)] for i in range(k*N)]

    for i in range(k*N) :
        for j in range(l) :
            ks[i][j] = TLWEncrypt(p,q,n,s,sigma,MultExtTore(p,Sprime[i],p/(B**j)))
    return bs,ks

In [107]:
p = 16
q = 64
l = 2
B = 4
n = 5
k = 5
sigma = 0.1
N = 4

s = [1,1,0,1,0]
S = [[randint(0,1) for _ in range(N)] for _ in range(k)]
bs,ks = loadKeys(p,q,B,l,N,sigma,k,S,s)

In [150]:
# c is a TLWE ciphertext : in TQ^{n+1}
# bs = TGGSW_S(s_i)
# ks in TQ^{n+1}
def bootstrapping(p,q,B,l,n,k,N,c,bs,ks,s) :
    print("c : ",c)
    V = [round(p*i/(2*N)) % p for i in range(N)]
    W = [round(p*i/(2*N)) % p for i in range(N)]
    a_tilde = [round(c[i]*2*N/q) % (2*N) for i in range(n)]
    x_tilde = round(c[n]*2*N/q) % (2*N)
    for i in range(n) :
        if (-x_tilde % (2*N) >= N) :
            return "Fail"
    print(a_tilde,x_tilde)
    
    #TEST############## 
    
    tmp = [0]*(N)
    tmp[-x_tilde % (2*N)] = 1 # tmp = X^{-x_tilde}
    W = MultPolyExt(q,N,tmp,W)
    for i in range(n):
        tmp = [0]*N # tmp = X^{a_tilde[i]}
        if (a_tilde[i]  % (2*N) < N) :
            tmp[a_tilde[i] % (2*N)] = 1
        else :
            tmp[a_tilde[i] % N] = - 1
        if(s[i] ==1):
            W = MultPolyExt(q,N,tmp,W)
    print("W = ",W)
    
    
    tmp = [0]*(N)
    tmp[-x_tilde % (2*N)] = 1 # tmp = X^{-x_tilde}
    Q = [[0]*N for i in range(k)] + [MultPolyExt(q,N,tmp,V)]
    for i in range(n):
        tmp = [0]*N # tmp = X^{a_tilde[i]}
        if (a_tilde[i]  % (2*N) < N) :
            tmp[a_tilde[i] % (2*N)] = 1
        else :
            tmp[a_tilde[i] % N] = - 1
        Q = CMUX(q,N,bs[i],Q,[MultPolyExt(q,N,tmp,Q[ind]) for ind in range(k+1)])
    C = Q
    print("C = ",C)
    
    print("Decrypt C = ", TGLWEDecrypt(p,q,N,k,S,C))
    
    
    #partie test
    print("Decrypt C (censé valoir Pn) :",TGLWEDecrypt(p,q,N,k,S,C))
    
    Cprime = []
    for i in range(k) :
        Cprime += [C[i][0]]
        for j in range(N-1,0,-1) :
            Cprime += [-C[i][j]]
    
    tmp = [0]*(n+1)
    for i in range(k*N) :
        for j in range(l) : 
            ks_opp = [-ks[i][j][index] for index in range(n+1)]
            Cbar_i = InvGVect(q,B,l,n,[Cprime[i]])[0]
            tmp2 = [MultExtTore(q,Cbar_i[j],ks_opp[ind]) for ind in range(n+1)]
            tmp = [AddInTore(q,tmp[index],tmp2[index]) for index in range(n+1)]
    return [AddInTore(q,tmp[index],([0]*(n) + [C[k][0]])[index]) for index in range(n+1)]

In [151]:

cpt = 0
for i in range(100):
    m = randint(0,p-1)
    c = TLWEncrypt(p, q, n, s, sigma, m)
    trux = bootstrapping(p,q,B,l,n,k,N,c,bs,ks,s)
    if (trux!="Fail") :
        truc = TLWEDecrypt(p,q,n,s,trux)
        #print(TLWEDecrypt(p,q,n,s,trux))
        #print("message clair :",m)
        if(truc==m):
            cpt +=1
print(cpt)

c :  [2, 4, 49, 30, 51, 43]
[0, 1, 6, 4, 6] 5
W =  [0, 2, 4, 6]
C =  [[37, 35, 40, 50], [45, 15, 51, 47], [17, 45, 34, 3], [22, 52, 2, 40], [46, 34, 58, 5], [45, 59, 53, 62]]
Decrypt C =  [14, 5, 12, 11]
Decrypt C (censé valoir Pn) : [14, 5, 12, 11]
c :  [3, 52, 5, 12, 57, 20]
c :  [61, 21, 41, 5, 29, 12]
c :  [21, 57, 26, 8, 39, 21]
c :  [31, 20, 17, 29, 62, 47]
[4, 3, 2, 4, 0] 6
W =  [6, 0, 62, 60]
C =  [[61, 62, 15, 27], [22, 6, 33, 34], [10, 48, 16, 42], [34, 13, 19, 57], [58, 38, 0, 6], [26, 44, 27, 51]]
Decrypt C =  [11, 14, 9, 15]
Decrypt C (censé valoir Pn) : [11, 14, 9, 15]
c :  [61, 17, 52, 26, 7, 35]
c :  [22, 2, 29, 11, 16, 46]
[3, 0, 4, 1, 2] 6
W =  [4, 6, 0, 62]
C =  [[41, 62, 44, 35], [20, 57, 28, 38], [17, 61, 58, 42], [37, 55, 3, 13], [1, 38, 44, 30], [48, 11, 30, 2]]
Decrypt C =  [15, 13, 13, 15]
Decrypt C (censé valoir Pn) : [15, 13, 13, 15]
c :  [40, 35, 29, 63, 51, 55]
[5, 4, 4, 0, 6] 7
W =  [60, 58, 0, 2]
C =  [[0, 0, 55, 15], [6, 34, 6, 8], [45, 59, 34, 27], [34,

C =  [[35, 44, 48, 10], [60, 20, 44, 34], [11, 11, 24, 2], [23, 41, 33, 18], [61, 57, 30, 31], [49, 14, 55, 61]]
Decrypt C =  [0, 10, 14, 5]
Decrypt C (censé valoir Pn) : [0, 10, 14, 5]
c :  [44, 59, 17, 7, 45, 33]
c :  [12, 50, 26, 57, 1, 28]
c :  [49, 51, 47, 55, 22, 31]
c :  [18, 15, 6, 21, 17, 10]
c :  [20, 44, 58, 49, 47, 52]
[3, 6, 7, 6, 6] 7
W =  [0, 2, 4, 6]
C =  [[63, 44, 28, 41], [46, 40, 63, 26], [16, 50, 51, 51], [4, 10, 6, 37], [53, 20, 23, 3], [9, 34, 35, 8]]
Decrypt C =  [10, 2, 5, 15]
Decrypt C (censé valoir Pn) : [10, 2, 5, 15]
c :  [46, 60, 28, 41, 35, 35]
c :  [21, 47, 28, 25, 8, 6]
c :  [14, 40, 22, 18, 25, 13]
2


In [125]:
while(1) :
    m = randint(0,p-1)
    print("Message : ",m)
    c = TLWEncrypt(p, q, n, s, sigma, m)

    K = randint(1,100)
    mmaybe = TLWEDecrypt(p, q, n, s, MultCiph(q,n,K,c))

    if(mmaybe==MultExtTore(p,K,m)):
        print("No need for bootstrapping")
    else :
        print("Need for bootstrapping")
        c_refresh = bootstrapping(p,q,B,l,n,k,N,c,bs,ks)
        mmaybe = TLWEDecrypt(p,q,n,s,c_refresh)
        print(mmaybe)

Message :  8
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  3
No need for bootstrapping
Message : 

Message :  14
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  7
No ne

Message :  1
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  2
No nee

Message :  12
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  12

Message :  8
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  4
No ne

...

Message :  13
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  4
No n

No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  11
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  12
No need for bo

No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  15
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  4
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  13
No need for bootstrapping
Message :  8
No need for bootstrappi

Message :  5
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  9
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  12
No need for bootstrapping
Message :  1
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  8
No need for bootstrapping
Message :  3
No need for bootstrapping
Message :  14
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  10
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  6
No need for bootstrapping
Message :  2
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  5
No need for bootstrapping
Message :  0
No need for bootstrapping
Message :  7
No need for bootstrapping
Message :  14
No nee

KeyboardInterrupt: 

In [ ]:
V = [round(p*i/(2*N)) % p for i in range(N)]
tmp = []